In [ ]:
!pip install -q probreg trimesh open3d cupy

In [1]:
import copy
import trimesh
import numpy as np
import cupy as xp
import open3d as o3d
from probreg.features import FPFH
from probreg import cpd, bcpd, filterreg
import plotly.graph_objects as go

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
def numpy_to_pointcloud(numpy_array):
    pcd = o3d.geometry.PointCloud()
    pcd.points = o3d.utility.Vector3dVector(numpy_array)
    return pcd

In [3]:
def to_point_cloud(mesh):
    vertices = mesh.vertices
    point_cloud = trimesh.points.PointCloud(vertices, colors=np.tile(np.array([0, 0, 0, 1]), (len(vertices), 1)))
    return point_cloud

def to_mesh(point_cloud, src_mesh):
    return trimesh.Trimesh(vertices=point_cloud.TY, faces=src_mesh.faces)

def add_colour(mesh):
    mesh.visual.vertex_colors = np.array([170, 51, 106, 255])
    return mesh

In [4]:
def draw_geometries(geometries):
    graph_objects = []

    for geometry in geometries:
        geometry_type = geometry.get_geometry_type()
        
        if geometry_type == o3d.geometry.Geometry.Type.PointCloud:
            points = np.asarray(geometry.points)
            colors = None
            if geometry.has_colors():
                colors = np.asarray(geometry.colors)
            elif geometry.has_normals():
                colors = (0.5, 0.5, 0.5) + np.asarray(geometry.normals) * 0.5
            else:
                geometry.paint_uniform_color((1.0, 0.0, 0.0))
                colors = np.asarray(geometry.colors)

            scatter_3d = go.Scatter3d(x=points[:,0], y=points[:,1], z=points[:,2], mode='markers', marker=dict(size=1, color=colors))
            graph_objects.append(scatter_3d)

        if geometry_type == o3d.geometry.Geometry.Type.TriangleMesh:
            triangles = np.asarray(geometry.triangles)
            vertices = np.asarray(geometry.vertices)
            colors = None
            if geometry.has_triangle_normals():
                colors = (0.5, 0.5, 0.5) + np.asarray(geometry.triangle_normals) * 0.5
                colors = tuple(map(tuple, colors))
            else:
                colors = (1.0, 0.0, 0.0)
            
            mesh_3d = go.Mesh3d(x=vertices[:,0], y=vertices[:,1], z=vertices[:,2], i=triangles[:,0], j=triangles[:,1], k=triangles[:,2], facecolor=colors, opacity=0.50)
            graph_objects.append(mesh_3d)
        
    fig = go.Figure(
        data=graph_objects,
        layout=dict(
            scene=dict(
                xaxis=dict(visible=False),
                yaxis=dict(visible=False),
                zaxis=dict(visible=False)
            )
        )
    )
    fig.show()

In [5]:
def transform(tf_param, points):
    points = (xp.asarray(points) + xp.dot(tf_param.g, tf_param.w)).get()
    return o3d.utility.Vector3dVector(points)

In [6]:
def downsample_mesh(mesh, points):
    faces = mesh.faces.shape[0]
    vertices = mesh.vertices.shape[0]
    factor = points / mesh.vertices.shape[0]
    new_faces = np.round(mesh.faces.shape[0] * factor)
    downsampled = mesh.simplify_quadratic_decimation(new_faces)
    return downsampled

In [19]:
max_n_points = 15000
target_file = '/kaggle/input/cns-imgreg/VH_F_Kidney_L.glb'
source_file = '/kaggle/input/cns-imgreg/VH_F_Kidney_R.glb'

In [20]:
target_mesh = trimesh.load(target_file, force='mesh')
target_mesh = downsample_mesh(target_mesh, min(max_n_points, target_mesh.vertices.shape[0]))
target = numpy_to_pointcloud(np.array(target_mesh.vertices))


source_mesh = trimesh.load(source_file, force='mesh')
source_mesh = downsample_mesh(source_mesh, min(max_n_points, target_mesh.vertices.shape[0]))
source = numpy_to_pointcloud(np.array((source_mesh).vertices))

In [ ]:
# target_mesh = trimesh.load('/kaggle/input/cns-imgreg/VH_F_Kidney_L_10K.glb', force='mesh')
# # target_sampled_points = trimesh.sample.sample_surface(target_mesh, 10000)
# # target_sampled_mesh = target_mesh.submesh([target_sampled_points[1]])[0]
# target = numpy_to_pointcloud(np.array(to_point_cloud(target_mesh).vertices))


# source_mesh = trimesh.load('/kaggle/input/cns-imgreg/VH_M_Kidney_L_10K.glb', force='mesh')
# # source_sampled_points = trimesh.sample.sample_surface(source_mesh, 10000)
# # source_sampled_mesh = source_mesh.submesh([source_sampled_points[1]])[0]
# source = numpy_to_pointcloud(np.array(to_point_cloud(source_mesh).vertices))

In [21]:
%%time

# compute cpd registration
out_transform = cpd.registration_cpd(source=source, target=target, maxiter=500, tol=1e-12, tf_type_name='nonrigid', use_cuda=True)
result = copy.deepcopy(source)
result.points = transform(out_transform.transformation, result.points)

CPU times: user 15min 50s, sys: 3min 32s, total: 19min 23s
Wall time: 19min 25s


In [22]:
result_mesh = trimesh.Trimesh(vertices=result.points, faces=source_mesh.faces)

In [23]:
source_mesh.show()

In [18]:
target_mesh.show()

In [11]:
result_mesh.show()

In [ ]:
result_mesh.show()

In [ ]:
# save result

# result_file = source_file.replace('.obj', '_REGISTERED_CPD.glb').replace('/kaggle/input/cns-imgreg', '/kaggle/working')
# _ = result_mesh.export(result_file)

# # save source
# source_downsampled_file = source_file.replace('.obj', f'_{max_n_points}.glb').replace('/kaggle/input/cns-imgreg', '/kaggle/working')
# _ = source_mesh.export(source_downsampled_file)

# # save target
# target_downsampled_file = target_file.replace('.glb', f'_{max_n_points}.glb').replace('/kaggle/input/cns-imgreg', '/kaggle/working')
# _ = target_mesh.export(target_downsampled_file)

In [ ]:
source.paint_uniform_color([1, 0, 0])
draw_geometries([source])

In [ ]:
target.paint_uniform_color([1, 0, 0])
draw_geometries([target])

In [ ]:
result.paint_uniform_color([1, 0, 0])
draw_geometries([result])